In [1]:
import lightgbm as lgb
import numpy as np
import optuna
import pandas as pd
import plotly.express as px
import plotly.graph_objs as go
import plotly.offline as pyo
import tensorflow as tf
import warnings
import xgboost as xgb
from lightgbm import LGBMRegressor
from math import sqrt
from sklearn.metrics import mean_squared_error, r2_score, explained_variance_score, mean_absolute_error
from sklearn.preprocessing import MinMaxScaler
from sklearn.decomposition import PCA
from keras.backend import clear_session
from keras.callbacks import EarlyStopping, ModelCheckpoint
from keras.layers import Dense, LSTM, Dropout, Flatten, Conv1D, TimeDistributed, RepeatVector
from keras.losses import MeanSquaredError
from keras.metrics import RootMeanSquaredError
from keras.models import Sequential, load_model
from keras.optimizers import Adam
warnings.simplefilter(action='ignore', category=(FutureWarning, UserWarning))

# Funções auxiliares

In [2]:
# Função para criar dados multivariados
def multivariate_data(
    dataset: np.ndarray,
    target: np.ndarray,
    start_index: int,
    end_index: int,
    history_size: int,
    target_size: int,
    step: int,
    single_step: bool = False
) -> tuple[np.ndarray, np.ndarray]:
    """Create multivariate data for time series forecasting.

    This function generates input data and corresponding target data for time series forecasting tasks.
    It can be used for both single-step and multi-step forecasting.
    The function is based on the TensorFlow tutorial: https://www.tensorflow.org/tutorials/structured_data/time_series#part_2_forecast_a_multivariate_time_series 

    Args:
        dataset (np.ndarray): The input dataset, typically a 2D array with shape (num_samples, num_features).
        target (np.ndarray): The target variable or values to predict, typically a 1D array with shape (num_samples,).
        start_index (int): The starting index of the data in the dataset array.
        end_index (int): The ending index of the data in the dataset array.
        history_size (int): The number of time steps to consider as history for each input data point.
        target_size (int): The number of future time steps to predict.
        step (int): The number of time steps to skip between data points in the history.
        single_step (bool, optional): If True, create data for single-step forecasting; if False, create data for multi-step forecasting. Defaults to False.

    Returns:
        tuple[np.ndarray, np.ndarray]: A tuple containing:
            - A 3D array of shape (num_samples, history_size, num_features) containing input data.
            - A 1D or 2D array (depending on single_step) containing target data.
              If single_step is True, it's a 1D array of shape (num_samples,) with the next time step's target.
              If single_step is False, it's a 2D array of shape (num_samples, target_size) with multi-step targets.

    Example:
        >>> data, labels = multivariate_data(
        ...     dataset=data_array,
        ...     target=target_array,
        ...     start_index=0,
        ...     end_index=100,
        ...     history_size=10,
        ...     target_size=1,
        ...     step=1,
        ...     single_step=True
        ... )
    """
    data = []
    labels = []
    start_index = start_index + history_size
    if end_index is None:
        end_index = len(dataset) - target_size
    for i in range(start_index, end_index):
        indices = range(i-history_size, i, step)
        data.append(dataset[indices])
        if single_step:
            labels.append(target[i + target_size])
        else:
            labels.append(target[i : i + target_size])

    return np.array(data), np.array(labels)

In [3]:
def metric_display(y_test, y_pred, idx_start = None, idx_end = None) -> None :
    """Exibe métricas de avaliação de um modelo de regressão e gera um gráfico de comparação.

    Esta função calcula várias métricas de avaliação de um modelo de regressão, incluindo RMSE, MAE, MAPE, SMAPE, R² e EVS.
    Além disso, ela cria um gráfico de linha para visualizar a comparação entre os valores reais (y_test) e os valores previstos (y_pred).

    Args:
        y_test (array-like): Os valores reais da variável de destino.
        y_pred (array-like): Os valores previstos pelo modelo.
        idx_start (str): A data e hora de início do período de teste.
        idx_end (str): A data e hora de término do período de teste.

    Returns:
        None

    Examples:
        >>> y_test = [3.0, 4.0, 5.0, 6.0, 7.0]
        >>> y_pred = [2.8, 4.2, 4.9, 6.3, 7.2]
        >>> metric_display(y_test, y_pred, idx_start='2021-01-01 00:00', idx_end='2021-01-01 04:00')
        
    """
    # Calcula o erro médio quadrático (RMSE)
    rmse = np.sqrt(mean_squared_error(y_test, y_pred))
    
    # Calcula o erro absoluto médio (MAE)
    mae = mean_absolute_error(y_test, y_pred)
    
    # Calcula o erro percentual absoluto médio (MAPE)
    mape = np.mean(np.abs((y_pred - y_test) / y_test)) * 100
    
    # Calcula o erro percentual absoluto médio simétrico (SMAPE)
    smape = 2 * np.mean(np.abs(y_pred - y_test) / (np.abs(y_pred) + np.abs(y_test))) * 100
    
    # Calcula o coeficiente de determinação (R²)
    r_squared = r2_score(y_test, y_pred)
    
    # Calcula a pontuação de variância explicada (EVS)
    evs = explained_variance_score(y_test, y_pred)

    print(f'[Menor é melhor] RMSE: {rmse:.4f}')
    print(f'[Menor é melhor] MAE: {mae:.4f}')
    print(f'[Menor é melhor] MAPE: {mape:.4f}%')
    print(f'[Menor é melhor] SMAPE: {smape:.4f}% ')
    print(f'[Maior é melhor] R²: {r_squared:.4f} ')
    print(f'[Maior é melhor] EVS: {evs:.4f} ')

    # Cria um índice para o período de teste com base nos parâmetros fornecidos
    if idx_start is not None and idx_end is not None:
        # Se as datas forem fornecidas, use-as para criar o índice de hora em hora
        idx = pd.date_range(start=idx_start, end=idx_end, freq='H')
    else:
        # Caso contrário, use índices numéricos padrão com base no comprimento dos dados
        idx = range(len(y_test))

    # Cria um DataFrame com o índice calculado
    df = pd.DataFrame({'Real (y_test)': y_test.ravel(), 'Previsto (y_pred)': y_pred.ravel()}, index=idx)

    # Gera um gráfico de comparação
    fig = px.line(df, title='Comparação entre y_test e y_pred',
                   labels={'value': 'Valor', 'variable': 'Valor'},
                   line_shape='linear')
    if idx_start is not None and idx_end is not None:
        fig.update_xaxes(title_text='Data e Hora', tickformat="%Y-%m-%d %H:%M")

    # Exibe o gráfico
    fig.show()

In [4]:
def plot_training_history(history):
    """
    Plota a história de treinamento de um modelo Keras usando Plotly. 

    Args:
        history (keras.callbacks.History): O objeto de história de treinamento do modelo Keras.

    Returns:
        None
    """
    # Extrair informações da história de treinamento
    train_loss = history.history['loss']
    val_loss = history.history['val_loss']

    # Converter o objeto de intervalo em lista
    epochs = list(range(1, len(train_loss) + 1))

    # Criar um gráfico interativo com proporção quadrada
    fig = go.Figure()

    # Adicionar curva de perda de treinamento
    fig.add_trace(go.Scatter(x=epochs, y=train_loss, mode='lines', name='Train Loss'))

    # Adicionar curva de perda de validação
    fig.add_trace(go.Scatter(x=epochs, y=val_loss, mode='lines', name='Validation Loss'))

    # Configurar o layout do gráfico
    fig.update_layout(
        title='Loss Over Epochs',
        xaxis_title='Epochs',
        yaxis_title='Loss',
        xaxis=dict(showgrid=True),
        yaxis=dict(showgrid=True),
        width=1000,
        height=600
    )

    # Exibir o gráfico
    fig.show()

# Carregar dados

In [5]:
# Carregar os dados
data = pd.read_csv('../TCC/datasets/forecast_dap.csv')
data['Timestamp'] = pd.to_datetime(data['Timestamp']).dt.strftime('%Y-%m-%d %H:%M')
data.set_index('Timestamp', inplace=True)

In [6]:
data.columns

Index(['Day Ahead Price', 'Biomass', 'Fossil Gas', 'Fossil Hard coal',
       'Fossil Oil', 'Hydro Pumped Storage', 'Hydro Run-of-river and poundage',
       'Hydro Water Reservoir', 'Nuclear', 'Solar', 'Waste', 'Wind Onshore',
       'Total Generation', 'Actual Load', 'BE', 'CH', 'DE_AT_LU', 'ES', 'GB',
       'IT_NORD', 'IT_NORD_FR', 'Total Flux', 'DE_LU', 'Weekday', 'Holiday'],
      dtype='object')

In [7]:
# Definindo a coluna alvo
target = 'Day Ahead Price'

# Seleção de features e Preparação para a modelagem

In [8]:
# Copiando o dataframe original para preservar os dados originais
df_final = data.copy()

# Definir o caminho para salvar os modelos
model_path = f'../TCC/modelos/{target.replace(" ", "_")}_'

# Criação dos conjuntos de treinamento, validação e teste
train_end_idx = df_final.index.get_loc('2023-01-01 00:00')  # Índice de término para treinamento
valid_end_idx = df_final.index.get_loc('2023-02-15 00:00')  # Índice de término para validação
test_end_idx = df_final.index.get_loc('2023-02-28 23:00')   # Índice de término para teste

# Separação dos dados de entrada e saída
X = df_final[df_final.columns.drop(target)].values # Dados de entrada
y = df_final[target].values.reshape(-1, 1)  # Dados de saída

# Inicialização e ajuste dos scalers para normalização dos dados
scaler_X = MinMaxScaler(feature_range=(0, 1))   # Inicialização do scaler para normalização dos dados de entrada
scaler_y = MinMaxScaler(feature_range=(0, 1))   # Inicialização do scaler para normalização dos dados de saída
scaler_X.fit(X[:train_end_idx]) # Ajuste ao conjunto de treinamento
scaler_y.fit(y[:train_end_idx]) # Ajuste ao conjunto de treinamento
X_norm = scaler_X.transform(X)  # Normalização dos dados de entrada
y_norm = scaler_y.transform(y)  # Normalização dos dados de saída

# Redução de dimensionalidade usando PCA
pca = PCA().fit(X_norm[:train_end_idx]) # Ajuste aos dados normalizados de entrada
num_components = len(pca.explained_variance_ratio_) # Número de componentes principais

# Plotagem da variância explicada pelo número de componentes principais
fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(1, num_components+1), y=np.cumsum(pca.explained_variance_ratio_), mode='lines', name='Cumulativa', marker_color='gray'))
fig.add_trace(go.Bar(x=np.arange(1, num_components+1), y=pca.explained_variance_ratio_, name='Individual', marker_color='blue'))
fig.update_layout(title='Variância explicada pelo número de componentes principais',
                  xaxis_title='Número de componentes principais',
                  yaxis_title='Variância explicada',
                  autosize=False, width=1000, height=600)
fig.show()

# Redução de dimensionalidade usando PCA com 80% de variância explicada mantida
pca = PCA(n_components=0.80).fit(X_norm[:train_end_idx]) # Ajuste aos dados normalizados de entrada
X_pca = pca.transform(X_norm) # Transformação dos dados normalizados de entrada

# Concatenação das características reduzidas pelo PCA e dos alvos normalizados
dataset_norm = np.concatenate((X_pca, y_norm), axis=1) # Concatenação das características reduzidas pelo PCA e dos alvos normalizados

# Definição do tamanho da janela de histórico e do tamanho do alvo futuro
past_history = 24 # Número de horas anteriores utilizado para prever o dado futuro
future_target = 0 # Se for 0, o modelo será de regressão, caso contrário, será de classificação

# Criação de conjuntos de treinamento, validação e teste usando a função 'multivariate_data'
X_train, y_train = multivariate_data(dataset_norm, dataset_norm[:, -1], 0, train_end_idx, past_history, future_target, step=1, single_step=True)
X_val, y_val = multivariate_data(dataset_norm, dataset_norm[:, -1], train_end_idx, valid_end_idx, past_history, future_target, step=1, single_step=True)
X_test, y_test = multivariate_data(dataset_norm, dataset_norm[:, -1], valid_end_idx, test_end_idx, past_history, future_target, step=1, single_step=True)

# Definição do tamanho do lote e do tamanho do buffer
batch_size = 32 # Número de amostras por atualização de gradiente (batch), menor mais lento, mas mais preciso (evita overfitting) 
buffer_size = 1000 # Tamanho do buffer para embaralhar os dados de treinamento, utilizado para datasets muito grandes

# Criação de conjunto de dados TensorFlow para treinamento e validação
# tf.data.Dataset.from_tensor_slices() cria um conjunto de dados a partir de um tensor
# cache() mantém os dados na memória após serem carregados do disco durante a primeira época
# shuffle() embaralha os dados para garantir que a ordem dos dados não afete o treinamento
# batch() agrupa os dados em lotes de tamanho igual
# prefetch() prepara os dados para a próxima iteração
train = tf.data.Dataset.from_tensor_slices((X_train, y_train)).cache().shuffle(buffer_size).batch(batch_size).prefetch(1) # Conjunto de treinamento
validation = tf.data.Dataset.from_tensor_slices((X_val, y_val)).batch(batch_size).prefetch(1) # Conjunto de validação

# Definição de parâmetros comuns aos modelos
input_shape = X_train.shape[-2:] # Formato dos dados de entrada (número de amostras, número de características)
loss = MeanSquaredError() # Função de perda (erro quadrático médio)
metric = [RootMeanSquaredError()] # Métrica (raiz quadrada do erro quadrático médio)
early_stopping = EarlyStopping(patience=10) # Parada antecipada (sem melhoria no erro quadrático médio por 10 épocas)

# Reformulação de 'y_test' para sua forma original e inversão da normalização
y_test = y_test.reshape(-1, 1) # Reformulação de 'y_test' para sua forma original
y_test_inv = scaler_y.inverse_transform(y_test) # Inversão da normalização de 'y_test'

# LGBM

In [9]:
# Reformular os dados de treinamento, validação e teste
X_train_lgb = X_train.reshape(-1, X_train.shape[1] * X_train.shape[2]) # Reformulação dos dados de treinamento para terem apenas 2 dimensões
X_val_lgb = X_val.reshape(-1, X_val.shape[1] * X_val.shape[2]) # Reformulação dos dados de validação para terem apenas 2 dimensões
X_test_lgb = X_test.reshape(-1, X_test.shape[1] * X_test.shape[2]) # Reformulação dos dados de teste para terem apenas 2 dimensões

# Defina a função de objetivo para otimização do Optuna
def objective(trial):
    
    # Defina os parâmetros a serem otimizados
    params = {
        "objective": "regression",
        "metric": "rmse",
        "random_state": 42,
        "force_col_wise": True,
        "verbosity": -1,
        "num_leaves": trial.suggest_int("num_leaves", 2, 64),
        "learning_rate": trial.suggest_loguniform("learning_rate", 0.001, 0.1),
        "n_estimators": trial.suggest_int("n_estimators", 100, 1000)
    }
    # Crie um modelo LGBMRegressor com os parâmetros definidos
    model = LGBMRegressor(**params)

    # Treine o modelo
    model.fit(X_train_lgb, y_train.ravel())

    # Faça previsões para o conjunto de validação
    forecast = model.predict(X_val_lgb)

    # Calcule o erro quadrático médio
    rmse = np.sqrt(mean_squared_error(y_val, forecast))

    return rmse

# Crie um estudo Optuna e otimize a função objetivo
study = optuna.create_study(direction="minimize")  # Minimize o RMSE
study.optimize(objective, n_trials=100)  # Execute 100 tentativas de otimização

# Obtenha os melhores hiperparâmetros encontrados
best_params = study.best_params

# Adicionando os parâmetros fixos, que não foram otimizados pelo Optuna
best_params.update({
    "objective": "regression",
    "metric": "rmse",
    "random_state": 42,
    "force_col_wise": True,
    "verbosity": -1
})

# Imprimir os melhores hiperparâmetros
print("Melhores Hiperparâmetros:", best_params)

[I 2023-10-25 20:32:26,181] A new study created in memory with name: no-name-d678e5f5-2855-4725-a82a-d681e9f16043
[I 2023-10-25 20:32:33,914] Trial 0 finished with value: 0.004537086283470821 and parameters: {'num_leaves': 6, 'learning_rate': 0.0074883754886997935, 'n_estimators': 569}. Best is trial 0 with value: 0.004537086283470821.
[I 2023-10-25 20:32:41,189] Trial 1 finished with value: 0.01979753482937737 and parameters: {'num_leaves': 32, 'learning_rate': 0.0013234388299518721, 'n_estimators': 217}. Best is trial 0 with value: 0.004537086283470821.
[I 2023-10-25 20:33:10,507] Trial 2 finished with value: 0.010960632045563893 and parameters: {'num_leaves': 32, 'learning_rate': 0.0010240456194150701, 'n_estimators': 922}. Best is trial 0 with value: 0.004537086283470821.
[I 2023-10-25 20:33:27,332] Trial 3 finished with value: 0.004190492048367423 and parameters: {'num_leaves': 18, 'learning_rate': 0.022464002635348257, 'n_estimators': 919}. Best is trial 3 with value: 0.004190492

Melhores Hiperparâmetros: {'num_leaves': 61, 'learning_rate': 0.006816187723407032, 'n_estimators': 792, 'objective': 'regression', 'metric': 'rmse', 'random_state': 42, 'force_col_wise': True, 'verbosity': -1}


In [10]:
# Use os melhores hiperparâmetros para treinar o modelo final
best_lgb_model = lgb.LGBMRegressor(**best_params)
best_lgb_model.fit(X_train_lgb, y_train.ravel())

# Salvar o modelo treinado
best_lgb_model.booster_.save_model(f"{model_path}lgbm_model.txt")

In [11]:
# Carregar o modelo
lgb_model = lgb.Booster(model_file=f"{model_path}lgbm_model.txt")

# Geração de previsões usando o modelo carregado
forecast = lgb_model.predict(X_test_lgb)

# Reformulação das previsões para o formato adequado e inversão da normalização
forecast = forecast.reshape(-1, 1)
lgb_pred = scaler_y.inverse_transform(forecast)

In [12]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, lgb_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 9.4536
[Menor é melhor] MAE: 7.4202
[Menor é melhor] MAPE: 5.6121%
[Menor é melhor] SMAPE: 5.6080% 
[Maior é melhor] R²: 0.8560 
[Maior é melhor] EVS: 0.8635 


# XGBOOST

In [13]:
# Reformulação dos conjuntos de treinamento, validação e teste para o formato adequado ao XGBoost
X_train_xgb = X_train.reshape(-1, X_train.shape[1] * X_train.shape[2])
X_val_xgb = X_val.reshape(-1, X_val.shape[1] * X_val.shape[2])
X_test_xgb = X_test.reshape(-1, X_test.shape[1] * X_test.shape[2])

# Defina a função de objetivo para otimização do Optuna
def objective(trial):
    param = {
        'objective': 'reg:squarederror',  # Para regressão
        'eval_metric': 'rmse',
        'silent': 1,
        'n_jobs': -1,
        'eta': trial.suggest_loguniform('eta', 0.001, 0.1),
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'subsample': trial.suggest_uniform('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_uniform('colsample_bytree', 0.5, 1.0),
        'alpha': trial.suggest_loguniform('alpha', 1e-5, 10.0),
        'lambda': trial.suggest_loguniform('lambda', 1e-5, 10.0),
        'gamma': trial.suggest_loguniform('gamma', 1e-5, 10.0),
        'min_child_weight': trial.suggest_loguniform('min_child_weight', 1e-5, 10.0)
    }
    
    # Criação de matrizes DMatrix para os conjuntos de treinamento, validação e teste do XGBoost
    dtrain = xgb.DMatrix(X_train_xgb, y_train)
    dval = xgb.DMatrix(X_val_xgb, y_val)
    
    # Lista de avaliação para acompanhar o desempenho do modelo XGBoost durante o treinamento
    evals = [(dtrain, 'train'), (dval, 'eval')]
    
    # Treinamento do modelo XGBoost com os parâmetros definidos
    model = xgb.train(param, dtrain, num_boost_round=1000, evals=evals, early_stopping_rounds=10, verbose_eval=False)

    # Geração de previsões usando o modelo XGBoost treinado
    forecast = model.predict(xgb.DMatrix(X_test_xgb))

    # Cálculo do erro quadrático médio
    rmse = np.sqrt(mean_squared_error(y_test, forecast))

    return rmse

# Crie um estudo Optuna e otimize a função objetivo
study = optuna.create_study(direction="minimize")  # Minimize o RMSE
study.optimize(objective, n_trials=100)  # Execute 100 tentativas de otimização

# Obtenha os melhores hiperparâmetros encontrados
best_params = study.best_params

# Adicionando os parâmetros fixos, que não foram otimizados pelo Optuna
best_params.update({
    'objective': 'reg:squarederror',
    'eval_metric': 'rmse',
    'silent': 1,
    'n_jobs': -1,
})

# Imprimir os melhores hiperparâmetros
print("Melhores Hiperparâmetros:", best_params)

[I 2023-10-25 21:11:33,031] A new study created in memory with name: no-name-dde39f69-36ea-442c-937a-d17909d00e9d
[I 2023-10-25 21:11:37,567] Trial 0 finished with value: 0.004226748541841818 and parameters: {'eta': 0.0525788057680964, 'max_depth': 8, 'subsample': 0.9268373446776288, 'colsample_bytree': 0.6613971199823063, 'alpha': 3.712511729300726, 'lambda': 8.24486281178486, 'gamma': 0.01723621170496009, 'min_child_weight': 0.0010237238752991043}. Best is trial 0 with value: 0.004226748541841818.
[I 2023-10-25 21:12:46,961] Trial 1 finished with value: 0.005090140645086005 and parameters: {'eta': 0.0019485304664497048, 'max_depth': 7, 'subsample': 0.5137757548717717, 'colsample_bytree': 0.6969987331707455, 'alpha': 0.1852062011150616, 'lambda': 1.2720577400891938e-05, 'gamma': 0.002344631582924973, 'min_child_weight': 0.0027292036071799954}. Best is trial 0 with value: 0.004226748541841818.
[I 2023-10-25 21:12:49,517] Trial 2 finished with value: 0.004460293049759242 and parameters:

Melhores Hiperparâmetros: {'eta': 0.004266907024057585, 'max_depth': 7, 'subsample': 0.7431417108247006, 'colsample_bytree': 0.5516142296497428, 'alpha': 0.013343752952889438, 'lambda': 0.04418296725719922, 'gamma': 4.150612857612374e-05, 'min_child_weight': 0.732391628651027, 'objective': 'reg:squarederror', 'eval_metric': 'rmse', 'silent': 1, 'n_jobs': -1}


In [14]:
# Use os melhores hiperparâmetros para treinar o modelo final
best_xgb_model = xgb.train(best_params, xgb.DMatrix(X_train_xgb, y_train), num_boost_round=1000, verbose_eval=False)

# Salvar o modelo treinado
best_xgb_model.save_model(f"{model_path}xgboost_model.model")

In [15]:
# Carregar o modelo salvo
loaded_xgb_model = xgb.Booster(model_file=f"{model_path}xgboost_model.model")

# Geração de previsões usando o modelo carregado
forecast = best_xgb_model.predict(xgb.DMatrix(X_test_xgb))

# Reformulação das previsões para o formato adequado e inversão da normalização
forecast = forecast.reshape(-1, 1)
xgb_pred = scaler_y.inverse_transform(forecast)

In [16]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, xgb_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 9.2699
[Menor é melhor] MAE: 7.3821
[Menor é melhor] MAPE: 5.6029%
[Menor é melhor] SMAPE: 5.5914% 
[Maior é melhor] R²: 0.8615 
[Maior é melhor] EVS: 0.8659 


In [17]:
# Reformulação dos conjuntos de treinamento, validação e teste para o formato adequado ao XGBoost
X_train_xgb = X_train.reshape(-1, X_train.shape[1] * X_train.shape[2])
X_val_xgb = X_val.reshape(-1, X_val.shape[1] * X_val.shape[2])
X_test_xgb = X_test.reshape(-1, X_test.shape[1] * X_test.shape[2])

# Definição dos parâmetros do modelo XGBoost
param = {'eta': 0.03,
         'max_depth': 180,
         'subsample': 1.0,
         'colsample_bytree': 0.95,
         'alpha': 0.1,
         'lambda': 0.15,
         'gamma': 0.1,
         'objective': 'reg:linear',
         'eval_metric': 'rmse',
         'silent': 1,
         'min_child_weight': 0.1,
         'n_jobs': -1
}

# Criação de matrizes DMatrix para os conjuntos de treinamento, validação e teste do XGBoost
dtrain = xgb.DMatrix(X_train_xgb, y_train)
dval = xgb.DMatrix(X_val_xgb, y_val)
dtest = xgb.DMatrix(X_test_xgb, y_test)

# Lista de avaliação para acompanhar o desempenho do modelo XGBoost durante o treinamento
eval_list = [(dtrain, 'train'), (dval, 'eval')]

# Treinamento do modelo XGBoost com os parâmetros definidos
xgb_model = xgb.train(param, dtrain, 180, eval_list, early_stopping_rounds=3)

# Geração de previsões usando o modelo XGBoost treinado
forecast = xgb_model.predict(dtest)

# Reformulação das previsões para o formato adequado e inversão da normalização
forecast = forecast.reshape(-1, 1)
xgb_pred = scaler_y.inverse_transform(forecast)

[0]	train-rmse:0.03156	eval-rmse:0.02545
[1]	train-rmse:0.03066	eval-rmse:0.02470
[2]	train-rmse:0.02979	eval-rmse:0.02399
[3]	train-rmse:0.02895	eval-rmse:0.02333
[4]	train-rmse:0.02813	eval-rmse:0.02265
[5]	train-rmse:0.02736	eval-rmse:0.02204
[6]	train-rmse:0.02659	eval-rmse:0.02139
[7]	train-rmse:0.02585	eval-rmse:0.02075
[8]	train-rmse:0.02513	eval-rmse:0.02014
[9]	train-rmse:0.02443	eval-rmse:0.01958
[10]	train-rmse:0.02376	eval-rmse:0.01902
[11]	train-rmse:0.02311	eval-rmse:0.01846
[12]	train-rmse:0.02249	eval-rmse:0.01792
[13]	train-rmse:0.02187	eval-rmse:0.01741
[14]	train-rmse:0.02128	eval-rmse:0.01690
[15]	train-rmse:0.02071	eval-rmse:0.01643
[16]	train-rmse:0.02016	eval-rmse:0.01594
[17]	train-rmse:0.01963	eval-rmse:0.01547
[18]	train-rmse:0.01911	eval-rmse:0.01503
[19]	train-rmse:0.01861	eval-rmse:0.01461
[20]	train-rmse:0.01813	eval-rmse:0.01421
[21]	train-rmse:0.01766	eval-rmse:0.01381
[22]	train-rmse:0.01722	eval-rmse:0.01342
[23]	train-rmse:0.01678	eval-rmse:0.01305
[2

In [18]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, xgb_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 11.9804
[Menor é melhor] MAE: 9.0762
[Menor é melhor] MAPE: 6.6047%
[Menor é melhor] SMAPE: 6.7649% 
[Maior é melhor] R²: 0.7687 
[Maior é melhor] EVS: 0.8124 


# LSTM

In [19]:
# Limpeza do ambiente do TensorFlow
clear_session()

# Definição do modelo
multivariate_lstm = Sequential([
    LSTM(100, input_shape=input_shape, return_sequences=True),
    Flatten(),
    Dense(200, activation='relu'),
    Dropout(0.1),
    Dense(1)
])

# Definição de Callbacks
model_checkpoint = ModelCheckpoint(f'{model_path}multivariate_lstm.h5', monitor=('val_loss'), save_best_only=True)
optimizer = Adam(learning_rate=6e-3, amsgrad=True)

# Compilação do modelo
multivariate_lstm.compile(loss=loss, optimizer=optimizer, metrics=metric)

In [20]:
# Treinamento do modelo
history = multivariate_lstm.fit(train, epochs=120, validation_data=validation, callbacks=[early_stopping, model_checkpoint])

Epoch 1/120
2188/2188 [==============================] - 45s 20ms/step - loss: 0.0191 - root_mean_squared_error: 0.1381 - val_loss: 0.0014 - val_root_mean_squared_error: 0.0378
Epoch 2/120
2188/2188 [==============================] - 45s 21ms/step - loss: 0.0037 - root_mean_squared_error: 0.0606 - val_loss: 0.0013 - val_root_mean_squared_error: 0.0365
Epoch 3/120
2188/2188 [==============================] - 44s 20ms/step - loss: 3.5434e-04 - root_mean_squared_error: 0.0188 - val_loss: 0.0015 - val_root_mean_squared_error: 0.0381
Epoch 4/120
2188/2188 [==============================] - 44s 20ms/step - loss: 3.5757e-04 - root_mean_squared_error: 0.0189 - val_loss: 0.0014 - val_root_mean_squared_error: 0.0370
Epoch 5/120
2188/2188 [==============================] - 43s 20ms/step - loss: 3.5730e-04 - root_mean_squared_error: 0.0189 - val_loss: 0.0014 - val_root_mean_squared_error: 0.0372
Epoch 6/120
2188/2188 [==============================] - 44s 20ms/step - loss: 3.5701e-04 - root_mean_s

In [21]:
# Plotagem da história de treinamento
plot_training_history(history)

In [22]:
# Carregamento do modelo com melhor desempenho
multivariate_lstm = load_model(f'{model_path}multivariate_lstm.h5')

# Geração de previsões usando o modelo treinado
forecast = multivariate_lstm.predict(X_test)
lstm_pred = scaler_y.inverse_transform(forecast)

10/10 [==============================] - 0s 5ms/step


In [23]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, lstm_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 104.3151
[Menor é melhor] MAE: 101.2975
[Menor é melhor] MAPE: 79.0132%
[Menor é melhor] SMAPE: 54.2289% 
[Maior é melhor] R²: -16.5384 
[Maior é melhor] EVS: 0.0000 


# STACKED LSTM

In [24]:
# Limpeza do ambiente do TensorFlow
clear_session()

# Definição do modelo
multivariate_stacked_lstm = Sequential([
    LSTM(250, input_shape=input_shape, return_sequences=True),
    LSTM(150, return_sequences=True),
    Flatten(),
    Dense(150, activation='relu'),
    Dropout(0.1),
    Dense(1)
])

# Definição de Callbacks
model_checkpoint = ModelCheckpoint(f'{model_path}multivariate_stacked_lstm.h5', save_best_only=True)
optimizer = Adam(learning_rate=3e-3, amsgrad=True)

# Compilação do modelo
multivariate_stacked_lstm.compile(loss=loss, optimizer=optimizer, metrics=metric)

In [25]:
# Treinamento do modelo
history = multivariate_stacked_lstm.fit(train, epochs=120, validation_data=validation, callbacks=[early_stopping, model_checkpoint])

Epoch 1/120
2188/2188 [==============================] - 172s 77ms/step - loss: 0.0018 - root_mean_squared_error: 0.0419 - val_loss: 7.4861e-04 - val_root_mean_squared_error: 0.0274
Epoch 2/120
2188/2188 [==============================] - 170s 78ms/step - loss: 3.2627e-04 - root_mean_squared_error: 0.0181 - val_loss: 0.0014 - val_root_mean_squared_error: 0.0369
Epoch 3/120
2188/2188 [==============================] - 172s 79ms/step - loss: 2.2841e-04 - root_mean_squared_error: 0.0151 - val_loss: 2.2239e-04 - val_root_mean_squared_error: 0.0149
Epoch 4/120
2188/2188 [==============================] - 172s 78ms/step - loss: 1.9249e-04 - root_mean_squared_error: 0.0139 - val_loss: 4.1408e-04 - val_root_mean_squared_error: 0.0203
Epoch 5/120
2188/2188 [==============================] - 173s 79ms/step - loss: 1.2193e-04 - root_mean_squared_error: 0.0110 - val_loss: 2.5325e-04 - val_root_mean_squared_error: 0.0159
Epoch 6/120
2188/2188 [==============================] - 174s 80ms/step - loss

In [26]:
# Plotagem da história de treinamento
plot_training_history(history)

In [27]:
# Carregamento do modelo com melhor desempenho
multivariate_stacked_lstm = load_model(f'{model_path}multivariate_stacked_lstm.h5')

# Geração de previsões usando o modelo treinado
forecast = multivariate_stacked_lstm.predict(X_test)
multivariate_stacked_lstm_pred = scaler_y.inverse_transform(forecast)

10/10 [==============================] - 1s 22ms/step


In [28]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, multivariate_stacked_lstm_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 11.6894
[Menor é melhor] MAE: 8.8080
[Menor é melhor] MAPE: 6.4361%
[Menor é melhor] SMAPE: 6.5475% 
[Maior é melhor] R²: 0.7798 
[Maior é melhor] EVS: 0.7846 


# CNN

In [29]:
# Limpeza do ambiente do TensorFlow
clear_session()

# Definição do modelo
multivariate_cnn = Sequential([
    Conv1D(filters=48, kernel_size=2, strides=1, padding='causal', activation='relu', input_shape=input_shape),
    Flatten(),
    Dense(48, activation='relu'),
    Dense(1)
])

# Definição de Callbacks
model_checkpoint = ModelCheckpoint(f'{model_path}multivariate_cnn.h5', save_best_only=True)
optimizer = Adam(learning_rate=6e-3, amsgrad=True)

# Compilação do modelo
multivariate_cnn.compile(loss=loss, optimizer=optimizer, metrics=metric)

In [30]:
# Treinamento do modelo
history = multivariate_cnn.fit(train, epochs=120, validation_data=validation, callbacks=[early_stopping, model_checkpoint])

Epoch 1/120
2188/2188 [==============================] - 6s 2ms/step - loss: 0.0015 - root_mean_squared_error: 0.0378 - val_loss: 1.2476e-04 - val_root_mean_squared_error: 0.0112
Epoch 2/120
2188/2188 [==============================] - 4s 2ms/step - loss: 8.1962e-05 - root_mean_squared_error: 0.0091 - val_loss: 2.3267e-04 - val_root_mean_squared_error: 0.0153
Epoch 3/120
2188/2188 [==============================] - 5s 2ms/step - loss: 6.1886e-05 - root_mean_squared_error: 0.0079 - val_loss: 1.0865e-04 - val_root_mean_squared_error: 0.0104
Epoch 4/120
2188/2188 [==============================] - 5s 2ms/step - loss: 6.5250e-05 - root_mean_squared_error: 0.0081 - val_loss: 1.5528e-04 - val_root_mean_squared_error: 0.0125
Epoch 5/120
2188/2188 [==============================] - 4s 2ms/step - loss: 6.1427e-05 - root_mean_squared_error: 0.0078 - val_loss: 1.2253e-04 - val_root_mean_squared_error: 0.0111
Epoch 6/120
2188/2188 [==============================] - 4s 2ms/step - loss: 5.3752e-05 -

In [31]:
# Plotagem da história de treinamento
plot_training_history(history)

In [32]:
# Carregamento do modelo com melhor desempenho
multivariate_cnn = load_model(f'{model_path}multivariate_cnn.h5')

# Geração de previsões usando o modelo treinado
forecast = multivariate_cnn.predict(X_test)
multivariate_cnn_pred = scaler_y.inverse_transform(forecast)

10/10 [==============================] - 0s 2ms/step


In [33]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, multivariate_cnn_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 17.8980
[Menor é melhor] MAE: 14.1846
[Menor é melhor] MAPE: 10.3761%
[Menor é melhor] SMAPE: 10.6476% 
[Maior é melhor] R²: 0.4837 
[Maior é melhor] EVS: 0.4838 


# CNN-LSTM

In [34]:
# Limpeza do ambiente do TensorFlow
clear_session()

# Definição do modelo
multivariate_cnn_lstm = Sequential([
    Conv1D(filters=100, kernel_size=2,
           strides=1, padding='causal',
           activation='relu', 
           input_shape=input_shape),
    LSTM(100, return_sequences=True),
    Flatten(),
    Dense(50, activation='relu'),
    Dense(1)
])

# Definição de Callbacks
model_checkpoint = ModelCheckpoint(f'{model_path}multivariate_cnn_lstm.h5', save_best_only=True)
optimizer = Adam(learning_rate=4e-3, amsgrad=True)

# Compilação do modelo
multivariate_cnn_lstm.compile(loss=loss, optimizer=optimizer, metrics=metric)

In [35]:
# Treinamento do modelo
history = multivariate_cnn_lstm.fit(train, epochs=120, validation_data=validation, callbacks=[early_stopping, model_checkpoint])

Epoch 1/120
2188/2188 [==============================] - 41s 18ms/step - loss: 0.0014 - root_mean_squared_error: 0.0374 - val_loss: 2.0889e-04 - val_root_mean_squared_error: 0.0145
Epoch 2/120
2188/2188 [==============================] - 45s 20ms/step - loss: 6.9632e-05 - root_mean_squared_error: 0.0083 - val_loss: 3.4118e-04 - val_root_mean_squared_error: 0.0185
Epoch 3/120
2188/2188 [==============================] - 40s 18ms/step - loss: 5.8450e-05 - root_mean_squared_error: 0.0076 - val_loss: 1.4648e-04 - val_root_mean_squared_error: 0.0121
Epoch 4/120
2188/2188 [==============================] - 40s 18ms/step - loss: 5.3801e-05 - root_mean_squared_error: 0.0073 - val_loss: 6.6456e-05 - val_root_mean_squared_error: 0.0082
Epoch 5/120
2188/2188 [==============================] - 39s 18ms/step - loss: 5.5704e-05 - root_mean_squared_error: 0.0075 - val_loss: 6.7205e-05 - val_root_mean_squared_error: 0.0082
Epoch 6/120
2188/2188 [==============================] - 40s 18ms/step - loss: 

In [36]:
# Plotagem da história de treinamento
plot_training_history(history)

In [37]:
# Carregamento do modelo com melhor desempenho
multivariate_cnn_lstm = load_model(f'{model_path}multivariate_cnn_lstm.h5')

# Geração de previsões usando o modelo treinado
forecast = multivariate_cnn_lstm.predict(X_test)
multivariate_cnn_lstm_pred = scaler_y.inverse_transform(forecast)

10/10 [==============================] - 0s 6ms/step


In [38]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, multivariate_cnn_lstm_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 14.1251
[Menor é melhor] MAE: 11.3720
[Menor é melhor] MAPE: 8.2741%
[Menor é melhor] SMAPE: 8.1060% 
[Maior é melhor] R²: 0.6784 
[Maior é melhor] EVS: 0.7027 


# TS MLP

In [39]:
# Limpeza do ambiente do TensorFlow
clear_session()

# Definição do modelo
multivariate_mlp = Sequential([
    TimeDistributed(Dense(200, activation='relu'),
                    input_shape=input_shape),
    TimeDistributed(Dense(150, activation='relu')),
    TimeDistributed(Dense(100, activation='relu')),
    TimeDistributed(Dense(50, activation='relu')),
    Flatten(),
    Dense(150, activation='relu'),
    Dropout(0.1),
    Dense(1)
])

# Definição de Callbacks
model_checkpoint = ModelCheckpoint(f'{model_path}multivariate_mlp.h5', save_best_only=True)
optimizer = Adam(learning_rate=2e-3, amsgrad=True)

# Compilação do modelo
multivariate_mlp.compile(loss=loss, optimizer=optimizer, metrics=metric)

In [40]:
# Treinamento do modelo
history = multivariate_mlp.fit(train, epochs=120, validation_data=validation, callbacks=[early_stopping, model_checkpoint])

Epoch 1/120
2188/2188 [==============================] - 12s 5ms/step - loss: 1.6862e-04 - root_mean_squared_error: 0.0129 - val_loss: 4.7344e-04 - val_root_mean_squared_error: 0.0218
Epoch 2/120
2188/2188 [==============================] - 12s 5ms/step - loss: 8.8351e-05 - root_mean_squared_error: 0.0094 - val_loss: 3.0521e-04 - val_root_mean_squared_error: 0.0175
Epoch 3/120
2188/2188 [==============================] - 11s 5ms/step - loss: 7.0914e-05 - root_mean_squared_error: 0.0084 - val_loss: 9.6527e-05 - val_root_mean_squared_error: 0.0098
Epoch 4/120
2188/2188 [==============================] - 11s 5ms/step - loss: 8.6795e-05 - root_mean_squared_error: 0.0093 - val_loss: 2.4760e-04 - val_root_mean_squared_error: 0.0157
Epoch 5/120
2188/2188 [==============================] - 11s 5ms/step - loss: 6.9187e-05 - root_mean_squared_error: 0.0083 - val_loss: 1.4664e-04 - val_root_mean_squared_error: 0.0121
Epoch 6/120
2188/2188 [==============================] - 11s 5ms/step - loss: 5.

In [41]:
# Plotagem da história de treinamento
plot_training_history(history)

In [42]:
# Carregamento do modelo com melhor desempenho
multivariate_mlp = load_model(f'{model_path}multivariate_mlp.h5')

# Geração de previsões usando o modelo treinado
forecast = multivariate_mlp.predict(X_test)
multivariate_mlp_pred = scaler_y.inverse_transform(forecast)

10/10 [==============================] - 0s 2ms/step


In [43]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, multivariate_mlp_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 14.9417
[Menor é melhor] MAE: 12.2058
[Menor é melhor] MAPE: 9.0913%
[Menor é melhor] SMAPE: 8.9196% 
[Maior é melhor] R²: 0.6402 
[Maior é melhor] EVS: 0.7029 


# ENCODER-DECODER

In [44]:
# Limpeza do ambiente do TensorFlow
clear_session()

# Definição do modelo
encoder_decoder = Sequential([
    LSTM(50, activation='relu', input_shape=input_shape),
    RepeatVector(past_history),
    LSTM(50, activation='relu', return_sequences=True),
    TimeDistributed(Dense(50, activation='relu')),
    Flatten(),
    Dense(25, activation='relu'),
    Dense(1)
])

# Definição de Callbacks
model_checkpoint = ModelCheckpoint(f'{model_path}encoder_decoder.h5', save_best_only=True)
optimizer = Adam(learning_rate=1e-3, amsgrad=True)

# Compilação do modelo
encoder_decoder.compile(loss=loss, optimizer=optimizer, metrics=metric)

In [45]:
# Treinamento do modelo
history = encoder_decoder.fit(train, epochs=50, validation_data=validation, callbacks=[early_stopping, model_checkpoint])

Epoch 1/50
2188/2188 [==============================] - 40s 17ms/step - loss: 8.0086e-05 - root_mean_squared_error: 0.0089 - val_loss: 4.3986e-04 - val_root_mean_squared_error: 0.0210
Epoch 2/50
2188/2188 [==============================] - 35s 16ms/step - loss: 6.0015e-05 - root_mean_squared_error: 0.0077 - val_loss: 2.6288e-04 - val_root_mean_squared_error: 0.0162
Epoch 3/50
2188/2188 [==============================] - 35s 16ms/step - loss: 6.7523e-05 - root_mean_squared_error: 0.0082 - val_loss: 1.3997e-04 - val_root_mean_squared_error: 0.0118
Epoch 4/50
2188/2188 [==============================] - 35s 16ms/step - loss: 4.4210e-05 - root_mean_squared_error: 0.0066 - val_loss: 8.1949e-05 - val_root_mean_squared_error: 0.0091
Epoch 5/50
2188/2188 [==============================] - 34s 16ms/step - loss: 3.9403e-05 - root_mean_squared_error: 0.0063 - val_loss: 8.4928e-05 - val_root_mean_squared_error: 0.0092
Epoch 6/50
2188/2188 [==============================] - 36s 16ms/step - loss: 4.

In [46]:
# Plotagem da história de treinamento
plot_training_history(history)

In [47]:
# Carregamento do modelo com melhor desempenho
encoder_decoder = load_model(f'{model_path}encoder_decoder.h5')

# Geração de previsões usando o modelo treinado
forecast = encoder_decoder.predict(X_test)
encoder_decoder_pred = scaler_y.inverse_transform(forecast)

10/10 [==============================] - 0s 9ms/step


In [48]:
# Exibição das métricas de avaliação e do gráfico de comparação
metric_display(y_test_inv, encoder_decoder_pred, df_final.index[valid_end_idx+past_history], df_final.index[test_end_idx-1])

[Menor é melhor] RMSE: 15.9550
[Menor é melhor] MAE: 13.1694
[Menor é melhor] MAPE: 9.7098%
[Menor é melhor] SMAPE: 9.7200% 
[Maior é melhor] R²: 0.5897 
[Maior é melhor] EVS: 0.6277 


# PLOT

In [49]:
# Separar os dados de treinamento, validação e teste
train_plot = df_final[target][:train_end_idx]
cv_plot = df_final[target][train_end_idx:valid_end_idx]
test_plot = df_final[target][valid_end_idx:test_end_idx]
xgb_plot = pd.Series(xgb_pred.ravel(), index=test_plot.index[past_history:])
lgbm_plot = pd.Series(lstm_pred.ravel(), index=test_plot.index[past_history:])
stacked_lgbm_plot = pd.Series(multivariate_stacked_lstm_pred.ravel(), index=test_plot.index[past_history:])
cnn_plot = pd.Series(multivariate_cnn_pred.ravel(), index=test_plot.index[past_history:])
cnn_lstm_plot = pd.Series(multivariate_cnn_lstm_pred.ravel(), index=test_plot.index[past_history:])
mlp_plot = pd.Series(multivariate_mlp_pred.ravel(), index=test_plot.index[past_history:])
encoder_decoder_plot = pd.Series(encoder_decoder_pred.ravel(), index=test_plot.index[past_history:])

# Criar traços para os dados de treinamento e teste
train_trace = go.Scatter(x=train_plot.index, y=train_plot, mode='lines', name='Dados de Treinamento', line=dict(color='blue'))
cv_trace = go.Scatter(x=cv_plot.index, y=cv_plot, mode='lines', name='Dados de Validação', line=dict(color='orange'))
test_trace = go.Scatter(x=test_plot.index, y=test_plot, mode='lines', name='Dados de Teste', line=dict(color='green'))
xgb_trace = go.Scatter(x=xgb_plot.index, y=xgb_plot, mode='lines', name='Previsões (XGBoost)', line=dict(color='red'))
lgbm_trace = go.Scatter(x=lgbm_plot.index, y=lgbm_plot, mode='lines', name='Previsões (LSTM)', line=dict(color='purple'))
multi_lgbm_trace = go.Scatter(x=stacked_lgbm_plot.index, y=stacked_lgbm_plot, mode='lines', name='Previsões (Multivariate Stacked LSTM)', line=dict(color='black'))
cnn_trace = go.Scatter(x=cnn_plot.index, y=cnn_plot, mode='lines', name='Previsões (CNN)', line=dict(color='pink'))
cnn_lstm_trace = go.Scatter(x=cnn_lstm_plot.index, y=cnn_lstm_plot, mode='lines', name='Previsões (CNN-LSTM)', line=dict(color='brown'))
mlp_trace = go.Scatter(x=mlp_plot.index, y=mlp_plot, mode='lines', name='Previsões (MLP)', line=dict(color='gray'))
encoder_decoder_trace = go.Scatter(x=encoder_decoder_plot.index, y=encoder_decoder_plot, mode='lines', name='Previsões (Encoder-Decoder)', line=dict(color='cyan'))


# Definir o layout do gráfico
layout = go.Layout(title='Previsão de Demanda',
                   xaxis=dict(title='Data e Hora'),
                   yaxis=dict(title='Demanda [kVA]]'))

# Criar a figura com os traços de treinamento, teste e previsões do melhor modelo
fig = go.Figure(data=[train_trace, cv_trace, test_trace, xgb_trace, lgbm_trace, multi_lgbm_trace, cnn_trace, cnn_lstm_trace, mlp_trace, encoder_decoder_trace], layout=layout)

# Plotar o gráfico
pyo.iplot(fig)